In [1]:
import gym
from gym.spaces import Dict, Discrete, Box, Tuple
import numpy as np


class SampleGym(gym.Env):
    def __init__(self, config={}):
        self.config = config
        self.action_space = Tuple((Discrete(2), Box(-10, 10, (2,))))
        self.observation_space = Box(-10, 10, (2, 2))
        self.p_done = config.get("p_done", 0.1)

    def reset(self):
        return self.observation_space.sample()

    def step(self, action):
        chosen_action = action[0]
        cnt_control = action[1][chosen_action]

        if chosen_action == 0:
            reward = cnt_control
        else:
            reward = -cnt_control - 1

        print(f"Action, {chosen_action} continuous ctrl {cnt_control}")
        return (
            self.observation_space.sample(),
            reward,
            bool(np.random.choice([True, False], p=[self.p_done, 1.0 - self.p_done])),
            {},
        )


if __name__ == "__main__":
    env = SampleGym()
    env.reset()
    env.step((1, [-1, 2.1]))  # should say use action 1 with 2.1
    env.step((0, [-1.1, 2.1]))  # should say use action 0 with -1.1

Action, 1 continuous ctrl 2.1
Action, 0 continuous ctrl -1.1


In [2]:
from mlagents_envs.environment import UnityEnvironment
from gym_unity.envs import UnityToGymWrapper
import numpy as np

ENV_PATH = "../Build-ParallelEnv/Aimbot-ParallelEnv"
WORKER_ID = 1
BASE_PORT = 2002

env = UnityEnvironment(
    file_name=ENV_PATH,
    seed=1,
    side_channels=[],
    worker_id=WORKER_ID,
    base_port=BASE_PORT,
)

trackedAgent = 0
env.reset()
BEHA_SPECS = env.behavior_specs
BEHA_NAME = list(BEHA_SPECS)[0]
SPEC = BEHA_SPECS[BEHA_NAME]
print(SPEC)

decisionSteps, terminalSteps = env.get_steps(BEHA_NAME)

if trackedAgent in decisionSteps:  # ゲーム終了していない場合、環境状態がdecision_stepsに保存される
    nextState = decisionSteps[trackedAgent].obs[0]
    reward = decisionSteps[trackedAgent].reward
    done = False
if trackedAgent in terminalSteps:  # ゲーム終了した場合、環境状態がterminal_stepsに保存される
    nextState = terminalSteps[trackedAgent].obs[0]
    reward = terminalSteps[trackedAgent].reward
    done = True
print(decisionSteps.agent_id)
print(terminalSteps)


In [ ]:
print("decisionSteps.agent_id",decisionSteps.agent_id)
# decisionSteps.agent_id [1 2 5 7]
print("decisionSteps.agent_id_to_index",decisionSteps.agent_id_to_index)
# decisionSteps.agent_id_to_index {1: 0, 2: 1, 5: 2, 7: 3}
print("decisionSteps.reward",decisionSteps.reward)
# decisionSteps.reward [0. 0. 0. 0.]
print("decisionSteps.action_mask",decisionSteps.action_mask)
'''
decisionSteps.action_mask [array([[False, False, False],
       [False, False, False],
       [False, False, False],
       [False, False, False]]), array([[False, False, False],
       [False, False, False],
       [False, False, False],
       [False, False, False]]), array([[False, False],
       [False, False],
       [False, False],
       [False, False]])]
'''
print("decisionSteps.obs", decisionSteps.obs[0][0])
'''decisionSteps.obs [array([[-15.994009 ,   1.       , -26.322788 ,   1.       ,   1.       ,
          1.       ,   1.       ,   1.       ,   1.       ,   2.       ,
          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,
          1.       ,   1.       ,   1.3519633,   1.6946528,   2.3051548,
          3.673389 ,   9.067246 ,  17.521473 ,  21.727095 ,  22.753294 ,
         24.167128 ,  25.905216 ,  18.35725  ,  21.02278  ,  21.053417 ,
          0.       ],
       [ -1.8809433,   1.       , -25.66834  ,   1.       ,   2.       ,
          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,
          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,
          1.       ,   1.       ,  16.768637 ,  23.414627 ,  22.04486  ,
         21.050663 ,  20.486784 ,  20.486784 ,  21.050665 ,  15.049731 ,
         11.578419 ,   9.695194 ,  20.398016 ,  20.368341 ,  20.398016 ,
...
         20.551746 ,  20.00118  ,  20.001116 ,  20.551594 ,  21.5222   ,
         17.707508 ,  14.86889  ,  19.914494 ,  19.885508 ,  19.914463 ,
          0.       ]], dtype=float32)]'''


decisionSteps.agent_id [1 2 5 7]
decisionSteps.agent_id_to_index {1: 0, 2: 1, 5: 2, 7: 3}
decisionSteps.reward [0. 0. 0. 0.]
decisionSteps.action_mask [array([[False, False, False],
       [False, False, False],
       [False, False, False],
       [False, False, False]]), array([[False, False, False],
       [False, False, False],
       [False, False, False],
       [False, False, False]]), array([[False, False],
       [False, False],
       [False, False],
       [False, False]])]
decisionSteps.obs [  0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0.          0.          0.          0.
   0.          0.          0. 

'decisionSteps.obs [array([[-15.994009 ,   1.       , -26.322788 ,   1.       ,   1.       ,\n          1.       ,   1.       ,   1.       ,   1.       ,   2.       ,\n          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,\n          1.       ,   1.       ,   1.3519633,   1.6946528,   2.3051548,\n          3.673389 ,   9.067246 ,  17.521473 ,  21.727095 ,  22.753294 ,\n         24.167128 ,  25.905216 ,  18.35725  ,  21.02278  ,  21.053417 ,\n          0.       ],\n       [ -1.8809433,   1.       , -25.66834  ,   1.       ,   2.       ,\n          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,\n          1.       ,   1.       ,   1.       ,   1.       ,   1.       ,\n          1.       ,   1.       ,  16.768637 ,  23.414627 ,  22.04486  ,\n         21.050663 ,  20.486784 ,  20.486784 ,  21.050665 ,  15.049731 ,\n         11.578419 ,   9.695194 ,  20.398016 ,  20.368341 ,  20.398016 ,\n...\n         20.551746 ,  20.00118  ,  20.001116 ,  20.551594 ,  21.

In [1]:
from AimbotEnv import Aimbot

ENV_PATH = "../Build-ParallelEnv/Aimbot-ParallelEnv"
WORKER_ID = 1
BASE_PORT = 2002

env = Aimbot(envPath=ENV_PATH,workerID= WORKER_ID,basePort= BASE_PORT)


In [8]:
import numpy as np
env.unity_observation_shape
(128, 4) + env.unity_observation_shape
env.reset()

(array([[  0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       ,   0.       ,   0.       ,   0.       ,   0.       ,
           0.       , -15.994009 ,   1.       , -26.322788 ,   1.       ,
           1.       ,   1.       ,   1.       ,   1.       ,   1.       ,
           2.       ,   1.       ,   1.       ,   1.       ,   1.       ,
           1.       ,   1.       ,   1.       ,   1.3519633,   1.6946528,
           2.3051548,   3.673389 ,   9.067246 ,  17.521473 ,  21.727095 ,
          22.753294 ,  24.167128 ,  25.905216 ,  18.35725  ,  21.02278  ,
          21.053417 ,   0.       , -15.994003 ,   1.       , -26.322784 ,
           1.       ,   1.       ,   1